## Script to import bridge data, calculate priorities and plot priorities

Script imports data from csv files, converts them to dataframes, and calculates priorities.

In [1]:
# Import dependencies

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.path import Path
import seaborn as sns
import cartopy.crs as ccrs
from cartopy.io.img_tiles import OSM, MapQuestOpenAerial, GoogleTiles
from cartopy.io.shapereader import Reader
import cartopy.feature as cfeature


#### Import data from csv files.

Data is not complete in either csv so both csv files are imported and merged together for complete info for all bridges.

In [2]:
Central = pd.read_csv('Assessment centralisation.csv')
Confirm = pd.read_csv('Bridge Stock Data .csv')
# Google = pd.read_csv('Google Import.csv')

Merge dataframes to create new dataframe named 'Merged'.

In [3]:
Merged = Confirm.merge(Central, how = 'left', on = ['feature_id'])

Inspect the dataframe to see the columns

In [4]:
Merged.head()

feature_id  site_code_x  plot_number_x feature_id.1 Structure No_x  \
0     ST0001     12402489      3003541.0       ST0001              1   
1     ST0002     12410645      3002415.0       ST0002              2   
2     ST0003     12425143      3001815.0       ST0003              3   
3     ST0004     12425181      3001704.0       ST0004              4   
4     ST0005     17225251      3001593.0       ST0005              5   

               Name_x               Structure Type_x Status_x   Easting  \
0             BAYFORD                      S:Culvert     Live  530191.0   
1         BAYFORDBURY                 S:River Bridge     Live  531567.0   
2  BALLS PARK CULVERT                      S:Culvert     Live  533636.0   
3     BEDWELL CULVERT                      S:Culvert     Live  528596.0   
4      CATHARINE FARM  S:Pipe (Small Span Structure)     Live  520366.0   

   Northing   ...   Structure No_y              Name_y  \
0  207688.0   ...                1             BAYFORD   
1  211119.0   ...                2         BAYFORDBURY   
2  212321.0   ...                3  BALLS PARK CULVERT   
3  207449.0   ...                4     BEDWELL CULVERT   
4  200833.0   ...                5      CATHARINE FARM   

                Structure Type_y Status_y Carries_y             Crosses_y  \
0                      S:Culvert     Live      U191         Bayford Brook   
1                 S:River Bridge     Live      B158         Bayford Brook   
2                      S:Culvert     Live      A414  Un-named Watercourse   
3                      S:Culvert     Live       C55  Un-named Watercourse   
4  S:Pipe (Small Span Structure)     Live       C84      Catherine Bourne   

   Maintaining Agent_y critical_bci_y length carries  
0  HERTFORDSHIRE (STR)            0.0   1.22    U191  
1  HERTFORDSHIRE (STR)          100.0   4.27    B158  
2  HERTFORDSHIRE (STR)          100.0   0.99    A414  
3  HERTFORDSHIRE (STR)          100.0   1.91     C55  
4  HERTFORDSHIRE (STR)          100.0   0.76     C84  

[5 rows x 35 columns]

Keep only the columns we want and delete other columns with info we aren't after.

In [5]:
Cols_to_keep = ['feature_id', 'Name_x', 'Structure Type_x', 'Status_x', 'Easting',
                'Northing', 'Maintaining Agent_x', 'Construction Year', 'Hertitage',
                'critical_bci_x', 'length', 'carries', 'Crosses_x']

In [6]:
Merged = Merged[Cols_to_keep]

Tidy up column names

In [7]:
Cols_tidy = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting',
                'Northing', 'Maintaining Agent', 'Construction Year', 'Hertitage',
                'critical_bci', 'length', 'Carries', 'Crosses']

In [8]:
Merged.columns = Cols_tidy

#### Assign a length score to each bridge based on its length

In [9]:
Merged['Length Score'] = np.where(Merged['length'] <= 20, 2, 0)
Merged['Length Score'] = np.where(Merged['length'] > 20, 3, Merged['Length Score'])
Merged['Length Score'] = np.where(Merged['length'] >= 50, 4, Merged['Length Score'])
Merged['Length Score'] = np.where(Merged['length'] > 200, 5, Merged['Length Score'])

In [10]:
Merged.head()

feature_id                Name                 Structure Type Status  \
0     ST0001             BAYFORD                      S:Culvert   Live   
1     ST0002         BAYFORDBURY                 S:River Bridge   Live   
2     ST0003  BALLS PARK CULVERT                      S:Culvert   Live   
3     ST0004     BEDWELL CULVERT                      S:Culvert   Live   
4     ST0005      CATHARINE FARM  S:Pipe (Small Span Structure)   Live   

    Easting  Northing    Maintaining Agent Construction Year    Hertitage  \
0  530191.0  207688.0  HERTFORDSHIRE (STR)        01/01/1800  Not Present   
1  531567.0  211119.0  HERTFORDSHIRE (STR)        01/01/1972  Not Present   
2  533636.0  212321.0  HERTFORDSHIRE (STR)        01/01/1973  Not Present   
3  528596.0  207449.0  HERTFORDSHIRE (STR)        01/01/1920  Not Present   
4  520366.0  200833.0  HERTFORDSHIRE (STR)        01/01/1960  Not Present   

   critical_bci  length Carries               Crosses  Length Score  
0         50.32    1.22    U191         Bayford Brook             2  
1        100.00    4.27    B158         Bayford Brook             2  
2        100.00    0.99    A414  Un-named Watercourse             2  
3        100.00    1.91     C55  Un-named Watercourse             2  
4        100.00    0.76     C84      Catherine Bourne             2

#### Assign scores to each bridge based on what it carries and what it crosses.

Assign a score of 5 to any structures with structure type 'S:Rail Bridge'.

Use regular expressions to find A10-99 roads, A100-999 roads, A1000-9999 roads, and B roads and assign score accordingly.

All other structures are assigned a score of 1.

In [11]:
Merged['Crosses Score'] = np.where(Merged['Structure Type'] == 'S:Rail Bridge', 5, 1)
Merged['Crosses Score'] = np.where(Merged['Crosses'].str.contains(pat = '^A[0-9]{2}', regex = True), 5, Merged['Crosses Score'])
Merged['Crosses Score'] = np.where(Merged['Crosses'].str.contains(pat = '^A[0-9]{3}', regex = True), 4, Merged['Crosses Score'])
Merged['Crosses Score'] = np.where(Merged['Crosses'].str.contains(pat = '^A[0-9]{4}', regex = True), 3, Merged['Crosses Score'])
Merged['Crosses Score'] = np.where(Merged['Crosses'].str.contains(pat = '^B[0-9]', regex = True), 2, Merged['Crosses Score'])

In [12]:
Merged['Carries Score'] = np.where(Merged['Carries'].str.contains(pat = '^A[0-9]{2}', regex = True), 5, 1)
Merged['Carries Score'] = np.where(Merged['Carries'].str.contains(pat = '^A[0-9]{3}', regex = True), 4, Merged['Carries Score'])
Merged['Carries Score'] = np.where(Merged['Carries'].str.contains(pat = '^A[0-9]{4}', regex = True), 3, Merged['Carries Score'])
Merged['Carries Score'] = np.where(Merged['Carries'].str.contains(pat = '^B[0-9]', regex = True), 2, Merged['Carries Score'])

Check the columns and values again

In [13]:
Merged.head()

feature_id                Name                 Structure Type Status  \
0     ST0001             BAYFORD                      S:Culvert   Live   
1     ST0002         BAYFORDBURY                 S:River Bridge   Live   
2     ST0003  BALLS PARK CULVERT                      S:Culvert   Live   
3     ST0004     BEDWELL CULVERT                      S:Culvert   Live   
4     ST0005      CATHARINE FARM  S:Pipe (Small Span Structure)   Live   

    Easting  Northing    Maintaining Agent Construction Year    Hertitage  \
0  530191.0  207688.0  HERTFORDSHIRE (STR)        01/01/1800  Not Present   
1  531567.0  211119.0  HERTFORDSHIRE (STR)        01/01/1972  Not Present   
2  533636.0  212321.0  HERTFORDSHIRE (STR)        01/01/1973  Not Present   
3  528596.0  207449.0  HERTFORDSHIRE (STR)        01/01/1920  Not Present   
4  520366.0  200833.0  HERTFORDSHIRE (STR)        01/01/1960  Not Present   

   critical_bci  length Carries               Crosses  Length Score  \
0         50.32    1.22    U191         Bayford Brook             2   
1        100.00    4.27    B158         Bayford Brook             2   
2        100.00    0.99    A414  Un-named Watercourse             2   
3        100.00    1.91     C55  Un-named Watercourse             2   
4        100.00    0.76     C84      Catherine Bourne             2   

   Crosses Score  Carries Score  
0              1              1  
1              1              2  
2              1              4  
3              1              1  
4              1              1

#### Assign a 'Route Score' to each structure as the max of the Carries and Crosses scores

In [14]:
Merged['Route Score'] = Merged[['Carries Score', 'Crosses Score']].max(axis=1)

Check columns and values

In [15]:
Merged.head()

feature_id                Name                 Structure Type Status  \
0     ST0001             BAYFORD                      S:Culvert   Live   
1     ST0002         BAYFORDBURY                 S:River Bridge   Live   
2     ST0003  BALLS PARK CULVERT                      S:Culvert   Live   
3     ST0004     BEDWELL CULVERT                      S:Culvert   Live   
4     ST0005      CATHARINE FARM  S:Pipe (Small Span Structure)   Live   

    Easting  Northing    Maintaining Agent Construction Year    Hertitage  \
0  530191.0  207688.0  HERTFORDSHIRE (STR)        01/01/1800  Not Present   
1  531567.0  211119.0  HERTFORDSHIRE (STR)        01/01/1972  Not Present   
2  533636.0  212321.0  HERTFORDSHIRE (STR)        01/01/1973  Not Present   
3  528596.0  207449.0  HERTFORDSHIRE (STR)        01/01/1920  Not Present   
4  520366.0  200833.0  HERTFORDSHIRE (STR)        01/01/1960  Not Present   

   critical_bci  length Carries               Crosses  Length Score  \
0         50.32    1.22    U191         Bayford Brook             2   
1        100.00    4.27    B158         Bayford Brook             2   
2        100.00    0.99    A414  Un-named Watercourse             2   
3        100.00    1.91     C55  Un-named Watercourse             2   
4        100.00    0.76     C84      Catherine Bourne             2   

   Crosses Score  Carries Score  Route Score  
0              1              1            1  
1              1              2            2  
2              1              4            4  
3              1              1            1  
4              1              1            1

#### Assign a 'BCI Score' to each structure based on their BCI value

In [16]:
Merged['BCI Score'] = np.where(Merged['critical_bci'] <= 40, 5, 5)
Merged['BCI Score'] = np.where(Merged['critical_bci'] > 40, 4, Merged['BCI Score'])
Merged['BCI Score'] = np.where(Merged['critical_bci'] > 65, 3, Merged['BCI Score'])
Merged['BCI Score'] = np.where(Merged['critical_bci'] > 80, 2, Merged['BCI Score'])
Merged['BCI Score'] = np.where(Merged['critical_bci'] > 90, 1, Merged['BCI Score'])

In [17]:
Merged.head()

feature_id                Name                 Structure Type Status  \
0     ST0001             BAYFORD                      S:Culvert   Live   
1     ST0002         BAYFORDBURY                 S:River Bridge   Live   
2     ST0003  BALLS PARK CULVERT                      S:Culvert   Live   
3     ST0004     BEDWELL CULVERT                      S:Culvert   Live   
4     ST0005      CATHARINE FARM  S:Pipe (Small Span Structure)   Live   

    Easting  Northing    Maintaining Agent Construction Year    Hertitage  \
0  530191.0  207688.0  HERTFORDSHIRE (STR)        01/01/1800  Not Present   
1  531567.0  211119.0  HERTFORDSHIRE (STR)        01/01/1972  Not Present   
2  533636.0  212321.0  HERTFORDSHIRE (STR)        01/01/1973  Not Present   
3  528596.0  207449.0  HERTFORDSHIRE (STR)        01/01/1920  Not Present   
4  520366.0  200833.0  HERTFORDSHIRE (STR)        01/01/1960  Not Present   

   critical_bci  length Carries               Crosses  Length Score  \
0         50.32    1.22    U191         Bayford Brook             2   
1        100.00    4.27    B158         Bayford Brook             2   
2        100.00    0.99    A414  Un-named Watercourse             2   
3        100.00    1.91     C55  Un-named Watercourse             2   
4        100.00    0.76     C84      Catherine Bourne             2   

   Crosses Score  Carries Score  Route Score  BCI Score  
0              1              1            1          4  
1              1              2            2          1  
2              1              4            4          1  
3              1              1            1          1  
4              1              1            1          1

### Set the maximum importance for all minor structures (walls, gantries etc.) to be 10

First check the list of unique structure types

In [18]:
# List the unique structure types
Struc_uniq = Merged['Structure Type'].unique()
Struc_uniq

array(['S:Culvert', 'S:River Bridge', 'S:Pipe (Small Span Structure)',
       'S:Footbridge', 'S:Road Bridge', 'S:Rail Bridge', 'S:Subway',
       'S:Retaining Wall', 'S:Viaduct', 'S:Sign/Gantry', 'S:Other',
       'S:Underpass', 'S:Tunnel', 'S:Embankment'], dtype=object)

In [19]:
Limit_score = ['S:Pipe (Small Span Structure)', 'S:Retaining Wall', 'S:Sign/Gantry', 'S:Other','S:Embankment']

Select the structure types we want to limit to importance of 10 and save them in a list 'Limit_score'.

In [20]:
Merged['Importance'] = Merged['Length Score']*Merged['Route Score']

In [21]:
Merged['Severity'] = Merged['BCI Score']

Check the values of the minor structures and if they go beyond 10

In [22]:
Merged.loc[(Merged['Structure Type'].isin(Limit_score)), ['Importance']].describe()

Importance
count  476.000000
mean     4.840336
std      4.945996
min      2.000000
25%      2.000000
50%      2.000000
75%      6.000000
max     25.000000

Select the cells where 'Structure Type' is in the Limit_score list AND the importance is greater than 10, then set those values to 10.

In [23]:
Merged.loc[(Merged['Structure Type'].isin(Limit_score)) & (Merged['Importance'] > 10), ['Importance']] = 10

Check the importance values of the minor structures

In [24]:
Merged.loc[(Merged['Structure Type'].isin(Limit_score)), ['Importance']].describe()

Importance
count  476.000000
mean     4.054622
std      2.946034
min      2.000000
25%      2.000000
50%      2.000000
75%      6.000000
max     10.000000

As can be seen the maximum values have now been limited to 10

In [25]:
Merged['Critical'] = np.where(Merged['Importance'] >= 20, True, False)

In [26]:
Merged['Total Score'] = Merged['Importance'] * Merged['Severity']

In [27]:
Merged['Radius'] = 10*Merged['Importance']**1.5+100

Extract values from the dataframe we want to plot.

Importance is a score based on the length and route score of the structure.

Severity is the score based on BCI

## Merge the lat and long data from Google Import

In [35]:
# Extract the data we're interested in
East = Merged['Easting'].values
North = Merged['Northing'].values
Importance = Merged['Importance'].values
Severity = Merged['Severity'].values
Total_score = Merged['Total Score'].values
Names = Merged['feature_id'].values

As the data we have has eastings and northings and not latitudes and longitudes convert the eastings and northings

### Note although Bokeh says to convert to Mercator projection for map tiles, the actual projection is web-mercator, therefore use GOOGLE_MERCATOR

In [36]:
bridge_crs = ccrs.OSGB()
merc = ccrs.GOOGLE_MERCATOR
bridge_lat = []
bridge_lon = []
for es, nth in zip(East, North):
    x, y = merc.transform_point(es, nth, bridge_crs)
    bridge_lon.append(x)
    bridge_lat.append(y)


In [37]:
Merged['Latitude'] = bridge_lat
Merged['Longitude'] = bridge_lon
Merged.head()

feature_id                Name                 Structure Type Status  \
0     ST0001             BAYFORD                      S:Culvert   Live   
1     ST0002         BAYFORDBURY                 S:River Bridge   Live   
2     ST0003  BALLS PARK CULVERT                      S:Culvert   Live   
3     ST0004     BEDWELL CULVERT                      S:Culvert   Live   
4     ST0005      CATHARINE FARM  S:Pipe (Small Span Structure)   Live   

    Easting  Northing    Maintaining Agent Construction Year    Hertitage  \
0  530191.0  207688.0  HERTFORDSHIRE (STR)        01/01/1800  Not Present   
1  531567.0  211119.0  HERTFORDSHIRE (STR)        01/01/1972  Not Present   
2  533636.0  212321.0  HERTFORDSHIRE (STR)        01/01/1973  Not Present   
3  528596.0  207449.0  HERTFORDSHIRE (STR)        01/01/1920  Not Present   
4  520366.0  200833.0  HERTFORDSHIRE (STR)        01/01/1960  Not Present   

   critical_bci      ...       Carries Score Route Score BCI Score  \
0         50.32      ...                   1           1         4   
1        100.00      ...                   2           2         1   
2        100.00      ...                   4           4         1   
3        100.00      ...                   1           1         1   
4        100.00      ...                   1           1         1   

   Importance  Severity  Critical  Total Score      Radius      Latitude  \
0           2         4     False            8  128.284271  6.755545e+06   
1           4         1     False            4  180.000000  6.761033e+06   
2           8         1     False            8  326.274170  6.762889e+06   
3           2         1     False            2  128.284271  6.755225e+06   
4           2         1     False            2  128.284271  6.744868e+06   

      Longitude  
0 -12837.313030  
1 -10475.044382  
2  -7086.686472  
3 -15417.910820  
4 -28937.250734  

[5 rows x 25 columns]

#### Save the dataframe to csv

In [38]:
Merged.to_csv('Bridges.csv')

Create function to scatter plot the bridges with colour based on 'Severity' and size based on 'Importance'

In [39]:
Merged.columns

Index(['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
       'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
       'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
       'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
       'Critical', 'Total Score', 'Radius', 'Latitude', 'Longitude'],
      dtype='object')

## Create a new dataset sorted by priority score

In [40]:
DF_Sorted = Merged.sort_values(by=['Total Score'])

In [41]:
DF_Sorted[-5:]

feature_id                      Name Structure Type Status   Easting  \
1471     ST1455              LANGTON ROAD  S:Road Bridge   Live  536934.0   
1485     ST1469         KINGSMEAD VIADUCT      S:Viaduct   Live  534746.0   
2245     ST2239   CHIPPERFIELD OVERBRIDGE  S:Road Bridge   Live  506047.0   
1542     ST1528     TRING PARK FOOTBRIDGE   S:Footbridge   Live  492605.0   
795      ST0824  GUNNELSWOOD ROAD RAILWAY  S:Rail Bridge   Live  522839.0   

      Northing    Maintaining Agent Construction Year    Hertitage  \
1471  208992.0  HERTFORDSHIRE (STR)        01/01/1974  Not Present   
1485  213512.0  HERTFORDSHIRE (STR)        01/01/1975  Not Present   
2245  202681.0  HERTFORDSHIRE (STR)        01/01/1993  Not Present   
1542  210839.0  HERTFORDSHIRE (STR)        01/01/1975  Not Present   
795   225704.0  HERTFORDSHIRE (STR)        01/01/1968  Not Present   

      critical_bci      ...       Carries Score Route Score BCI Score  \
1471         58.00      ...                   1           5         4   
1485         55.48      ...                   5           5         4   
2245          0.00      ...                   1           5         5   
1542         39.52      ...                   1           5         5   
795          28.08      ...                   3           5         5   

      Importance  Severity  Critical  Total Score       Radius      Latitude  \
1471          20         4      True           80   994.427191  6.757363e+06   
1485          25         4      True          100  1350.000000  6.764767e+06   
2245          20         5      True          100   994.427191  6.748370e+06   
1542          20         5      True          100   994.427191  6.761983e+06   
795           20         5      True          100   994.427191  6.785010e+06   

         Longitude  
1471  -1912.657564  
1485  -5244.625333  
2245 -51926.958601  
1542 -73336.919557  
795  -23976.176598  

[5 rows x 25 columns]

# Bokeh testing

In [42]:
import holoviews as hv
from bokeh.plotting import figure, output_file, show
from bokeh.models.glyphs import Rect
from bokeh.io import output_notebook
from bokeh.models import HoverTool, Panel, Legend
from bokeh.models import ColumnDataSource, CDSView, BooleanFilter
from bokeh.models import LinearColorMapper, ColorBar, BasicTicker, PrintfTickFormatter, CustomJS, CategoricalColorMapper
from bokeh.models.widgets import CheckboxGroup, CheckboxButtonGroup, Slider, Tabs, TextInput
from bokeh.models.widgets import Button, RangeSlider, Dropdown, DataTable, TableColumn
from bokeh.layouts import column, row, WidgetBox
from bokeh.models import Title
from bokeh.layouts import gridplot
from bokeh.tile_providers import CARTODBPOSITRON_RETINA, STAMEN_TERRAIN
import matplotlib as mpl
from collections import OrderedDict
from bokeh.io import curdoc
from bokeh.palettes import Category20

from bokeh.application.handlers import FunctionHandler
from bokeh.application import Application
output_notebook()

Loading BokehJS ...

In [42]:
from bokeh.plotting import figure, show, output_file
from bokeh.tile_providers import CARTODBPOSITRON

output_file("tile.html")

# range bounds supplied in web mercator coordinates
p = figure(x_range=(-2000000, 6000000), y_range=(-1000000, 7000000),
           x_axis_type="mercator", y_axis_type="mercator")
p.add_tile(STAMEN_TERRAIN)

show(p)

In [43]:
from bokeh.models import WMTSTileSource

## Non-critical bridges

In [35]:
# prepare some data

x = Merged['Easting'].values
y = Merged['Northing'].values
axis_range = x.max()-x.min()
half_range = axis_range/2
y_mid = y.max() - (y.max()-y.min())/2
radii = Importance**2
color_list = [i for i in range(1, 101)]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(color_list))
]
map = {i:clr for i, clr in enumerate(colors)}


TOOLS = "crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,hover"

source = ColumnDataSource(Merged[Merged['Importance'] < 20])
# source2 = ColumnDataSource(Merged[Merged['Importance'] >= 20])
# s2 = ColumnDataSource(data={key: [] for key in Merged.keys()})

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below')

# p.add_tile(STAMEN_TERRAIN)

mapper = LinearColorMapper(palette=colors, low=1, high=100)

# add a circle renderer with vectorized colors and sizes
p.circle('Easting', 'Northing', source=source, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

# p_filtered = figure(tools=TOOLS, x_range=p.x_range, y_range=p.y_range, toolbar_location='below')
# p_filtered.circle('Easting', 'Northing', source=source2, radius='Radius', hover_color='red',
#          fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

p.title.text = "Non-critical bridges"
p.title.align = "center"
p.title.text_color = "black"
p.title.text_font_size = "25px"



p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "0pt"
p.axis.major_label_standoff = 0

# p_filtered.title.text = "Critical Bridges"
# p_filtered.title.align = "center"
# p_filtered.title.text_color = "black"
# p_filtered.title.text_font_size = "25px"

# p_filtered.axis.major_tick_line_color = None
# p_filtered.axis.major_label_text_font_size = "0pt"
# p_filtered.axis.major_label_standoff = 0



TOOLS="crosshair,pan,wheel_zoom,box_zoom,reset,hover"

hover =p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Importance", "@Importance"),
    ("BCI", "@Severity")])


color_bar = ColorBar(color_mapper=mapper, major_label_text_font_size="5pt",
                     ticker=BasicTicker(desired_num_ticks=int(len(colors)/5)),
                     label_standoff=6, border_line_color=None, location=(0, 0))


p.add_layout(color_bar, 'right')
# p_filtered.add_layout(color_bar2, 'right')

def radius_callback(source=source, window=None):
    f=cb_obj.value
    data = source.data
    Imp = data['Importance']
    rad = data['Radius']
    for i in range(len(rad)):
        rad[i] = f*Imp[i]**1.5+100
    source.change.emit()

# Slider to select the radius scaler, value is selected number
radius_select = Slider(start = 0, end = 10, 
                     step = 0.1, value = 1,
                     title = 'Radius scaler',
                       callback=CustomJS.from_py_func(radius_callback))



# Update the plot when the value is changed
# radius_select.on_change('value', update)

# def callback(source=source):
#     data = source.data
#     f = cb_obj.active
#     struc = data['Structure Type']
#     imp = data['Importance']
#     for i in range(len(imp)):
#         if struc[i] in f:
#             data['Importance'] = 0
#             data['Radius'] = 0
#     source.change.emit()

# struc_selection = CheckboxGroup(labels=list(Merged['Structure Type'].unique()),
#                                 active=[i for i in range(len(Merged['Structure Type'].unique()))], callback=CustomJS.from_py_func(struc_callback))


# struc_selection.on_change('active', struc_callback)

# def struc_callback(source=source, window=None):
#     act = [cb_obj.labels[i] for i in cb_obj.active]
#     data = source.data
#     Imp = data['Importance']
#     rad = data['Radius']
#     for i in range(len(rad)):
#         rad[i] = f*Imp[i]**2+100
#     source.change.emit()

# crit_select = Button(
#         label="Critical", button_type="success", callback=CustomJS.from_py_func(crit_callback))

# crit_select.js_on_click(crit_callback)

# crit_callback = CustomJS(args=dict(s2=s2), code="""
#         var inds = cb_obj.selected.indices;
#         var d1 = cb_obj.data;
#         var d2 = s2.data;
#         d2['x'] = []
#         d2['y'] = []
#         for (var i = 0; i < inds.length; i++) {
#             d2['x'].push(d1['x'][inds[i]])
#             d2['y'].push(d1['y'][inds[i]])
#         }
#         s2.change.emit();
#     """)

# crit_select.on_change('active', update)

# Put controls in a single element
controls = WidgetBox(radius_select)

# Create a row layout

layout = row(controls, p)

# tab1 = Panel(child=layout1, title="Non-Critical")

# tab2 = Panel(child=layout2, title="Critical")

# tabs = Tabs(tabs=[ tab1, tab2 ])

output_file("HCC Bridges non crit.html")

# show the results
# show(gridplot([[p, p_filtered]]))
show(layout)

## Range of importance

In [36]:
# prepare some data

x = Merged['Easting'].values
y = Merged['Northing'].values
axis_range = x.max()-x.min()
half_range = axis_range/2
y_mid = y.max() - (y.max()-y.min())/2
radii = Importance**2
color_list = [i for i in range(1, 101)]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(color_list))
]
map = {i:clr for i, clr in enumerate(colors)}


TOOLS = "crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,hover"

source = ColumnDataSource(DF_Sorted)
# source2 = ColumnDataSource(Merged[Merged['Importance'] >= 20])
s2 = ColumnDataSource(DF_Sorted)

s3 = ColumnDataSource({'x': [], 'y': [], 'width': [], 'height': []})

jscode="""
    var data = source.data;
    var start = cb_obj.start;
    var end = cb_obj.end;
    data['%s'] = [start + (end - start) / 2];
    data['%s'] = [end - start];
    source.change.emit();
"""

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below')

# p.add_tile(STAMEN_TERRAIN)

mapper = LinearColorMapper(palette=colors, low=1, high=100)

# add a circle renderer with vectorized colors and sizes
p.circle('Easting', 'Northing', source=s2, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.5, hover_alpha=0.8, line_color=None)


p.title.text = "HCC bridges"
p.title.align = "center"
p.title.text_color = "black"
p.title.text_font_size = "25px"

p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "0pt"
p.axis.major_label_standoff = 0

p.add_layout(Title(text="Colour Bar = Priority Score", align="center"), "right")

p.x_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('x', 'width'))
p.y_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('y', 'height'))

# create a new plot with the tools above, and explicit ranges
p2 = figure(tools='', x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below')

# add a circle renderer with vectorized colors and sizes
p2.circle('Easting', 'Northing', source=source, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.5, hover_alpha=0.8, line_color=None)

# p_filtered = figure(tools=TOOLS, x_range=p.x_range, y_range=p.y_range, toolbar_location='below')
# p_filtered.circle('Easting', 'Northing', source=source2, radius='Radius', hover_color='red',
#          fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

p2.title.text = "See Zoom Window Here"
p2.title.align = "center"
p2.title.text_color = "black"
p2.title.text_font_size = "25px"

p2.axis.major_tick_line_color = None
p2.axis.major_label_text_font_size = "0pt"
p2.axis.major_label_standoff = 0

rect = Rect(x='x', y='y', width='width', height='height', fill_alpha=0.1,
            line_color='black', fill_color='black')

p2.add_glyph(s3, rect)

TOOLS="crosshair,pan,wheel_zoom,box_zoom,reset,hover"

hover =p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Importance", "@Importance"),
    ("BCI", "@Severity")])


color_bar = ColorBar(color_mapper=mapper, major_label_text_font_size="5pt",
                     ticker=BasicTicker(desired_num_ticks=int(len(colors)/5)),
                     label_standoff=6, border_line_color=None, location=(0, 0))



p.add_layout(color_bar, 'right')
# p_filtered.add_layout(color_bar2, 'right')

def radius_callback(source=s2, window=None):
    f=cb_obj.value
    data = source.data
    Imp = data['Importance']
    rad = data['Radius']
    for i in range(len(rad)):
        rad[i] = f*Imp[i]**1.5+100
    source.change.emit()

# Slider to select the radius scaler, value is selected number
radius_select = Slider(start = 0, end = 20, 
                     step = 0.1, value = 10,
                     title = 'Radius scaler',
                       callback=CustomJS.from_py_func(radius_callback))

def range_callback(source=source, s2=s2, window=None):
    columns = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
               'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
               'Total Score', 'Latitude', 'Longitude', 'Critical', 'Radius']
    data = source.data
    data2 = s2.data        
    range_start = int(cb_obj.value[0])
    range_end = int(cb_obj.value[1])
    assert range_end > range_start
    for name in columns:
        data2[name] = []
    for name in columns:
        for i in range(range_start, range_end):
            data2[name].append(data[name][i])
    s2.change.emit()

selection = RangeSlider(start=1, end=2523, value=(1,2523), step=1, title="Structures",
                       callback=CustomJS.from_py_func(range_callback))



str0 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:River Bridge'])
str1 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Culvert'])
str2 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Subway'])
str3 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Footbridge'])
str4 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Retaining Wall'])
str5 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Pipe (Small Span Structure)'])
str6 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Sign/Gantry'])
str7 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Road Bridge'])
str8 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Viaduct'])
str9 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Underpass'])
str10 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Other'])
str11 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Embankment'])
str12 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Tunnel'])
str13 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Rail Bridge'])


def struc_callback(source=source, s2=s2, str0=str0, str1=str1, str3=str3, str4=str4,
                   str5=str5, str6=str6, str7=str7, str8=str8, str9=str9, str10=str10,
                   str11=str11, str12=str12, str13=str13, window=None):
    data = source.data
    data2 = s2.data
    length = len(data2['Structure Type'])
    value = cb_obj.value
    columns = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
               'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
               'Total Score', 'Latitude', 'Longitude', 'Critical', 'Radius']
    for name in columns:
        data2[name] = []
    for name in columns:
        for i in range(length):
            if value == 'S:River Bridge':
                data2[name] = str0.data[name]
            if value == 'S:Culvert':
                data2[name] = str1.data[name]
            if value == 'S:Subway':
                data2[name] = str2.data[name]
            if value == 'S:Footbridge':
                data2[name] = str3.data[name]
            if value == 'S:Retaining Wall':
                data2[name] = str4.data[name]
            if value == 'S:Pipe (Small Span Structure)':
                data2[name] = str5.data[name]
            if value == 'S:Sign/Gantry':
                data2[name] = str6.data[name]
            if value == 'S:Road Bridge':
                data2[name] = str7.data[name]
            if value == 'S:Viaduct':
                data2[name] = str8.data[name]
            if value == 'S:Underpass':
                data2[name] = str9.data[name]
            if value == 'S:Other':
                data2[name] = str10.data[name]
            if value == 'S:Embankment':
                data2[name] = str11.data[name]
            if value == 'S:Tunnel':
                data2[name] = str12.data[name]
            if value == 'S:Rail Bridge':
                data2[name] = str13.data[name]
            if value == 'All':
                data2[name] = data[name]
    s2.change.emit()

menu = [(struc, struc) for struc in DF_Sorted['Structure Type'].unique()]
menu.append(('All', 'All'))

struc_labels =[struc for struc in DF_Sorted['Structure Type'].unique()]

dropdown = Dropdown(label='Structure Type', menu=menu, button_type="success", callback=CustomJS.from_py_func(struc_callback))      


wanted_columns = ['feature_id', 'Name', 'Structure Type', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance',
               'Total Score']
columns = [TableColumn(field=str(value), title=value) for value in wanted_columns]
data_table = DataTable(source=source, columns=columns, width=1200, height=1000)


# Put controls in a single element
controls = WidgetBox(radius_select, selection, dropdown)

# Create a row layout

layout = row(controls, p, p2)

tab1 = Panel(child=layout, title="Plots")

tab2 = Panel(child=data_table, title="Data")

tabs = Tabs(tabs=[ tab1, tab2 ])

output_file("HCC Bridges Plot.html")

# show the results
# show(gridplot([[p, p_filtered]]))
show(tabs)

## Plot with Mercator projection and map background

In [42]:
# prepare some data

x = DF_Sorted['Longitude'].values
y = DF_Sorted['Latitude'].values
axis_range = x.max()-x.min()
half_range = axis_range/2
y_mid = y.max() - (y.max()-y.min())/2
radii = Importance**2
color_list = [i for i in range(1, 101)]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(color_list))
]
map = {i:clr for i, clr in enumerate(colors)}


TOOLS = "crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,hover"

source = ColumnDataSource(DF_Sorted)
# source2 = ColumnDataSource(Merged[Merged['Importance'] >= 20])
s2 = ColumnDataSource(DF_Sorted)

s3 = ColumnDataSource({'x': [], 'y': [], 'width': [], 'height': []})

jscode="""
    var data = source.data;
    var start = cb_obj.start;
    var end = cb_obj.end;
    data['%s'] = [start + (end - start) / 2];
    data['%s'] = [end - start];
    source.change.emit();
"""

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below',
          x_axis_type="mercator", y_axis_type="mercator")

p.add_tile(CARTODBPOSITRON_RETINA)

mapper = LinearColorMapper(palette=colors, low=1, high=100)

# add a circle renderer with vectorized colors and sizes
p.circle('Longitude', 'Latitude', source=s2, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.5, hover_alpha=0.8, line_color=None)


p.title.text = "HCC bridges"
p.title.align = "center"
p.title.text_color = "black"
p.title.text_font_size = "25px"

p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "0pt"
p.axis.major_label_standoff = 0

p.add_layout(Title(text="Colour Bar = Priority Score", align="center"), "right")

p.x_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('x', 'width'))
p.y_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('y', 'height'))

# create a new plot with the tools above, and explicit ranges
p2 = figure(tools='', x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below',
           x_axis_type="mercator", y_axis_type="mercator")

p2.add_tile(CARTODBPOSITRON_RETINA)

# add a circle renderer with vectorized colors and sizes
p2.circle('Longitude', 'Latitude', source=source, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.5, hover_alpha=0.8, line_color=None)

# p_filtered = figure(tools=TOOLS, x_range=p.x_range, y_range=p.y_range, toolbar_location='below')
# p_filtered.circle('Easting', 'Northing', source=source2, radius='Radius', hover_color='red',
#          fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

p2.title.text = "See Zoom Window Here"
p2.title.align = "center"
p2.title.text_color = "black"
p2.title.text_font_size = "25px"

p2.axis.major_tick_line_color = None
p2.axis.major_label_text_font_size = "0pt"
p2.axis.major_label_standoff = 0

rect = Rect(x='x', y='y', width='width', height='height', fill_alpha=0.1,
            line_color='black', fill_color='black')

p2.add_glyph(s3, rect)

TOOLS="crosshair,pan,wheel_zoom,box_zoom,reset,hover"

hover =p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Importance", "@Importance"),
    ("BCI", "@Severity")])


color_bar = ColorBar(color_mapper=mapper, major_label_text_font_size="5pt",
                     ticker=BasicTicker(desired_num_ticks=int(len(colors)/5)),
                     label_standoff=6, border_line_color=None, location=(0, 0))



p.add_layout(color_bar, 'right')
# p_filtered.add_layout(color_bar2, 'right')

def radius_callback(source=s2, window=None):
    f=cb_obj.value
    data = source.data
    Imp = data['Importance']
    rad = data['Radius']
    for i in range(len(rad)):
        rad[i] = f*Imp[i]**1.5+100
    source.change.emit()

# Slider to select the radius scaler, value is selected number
radius_select = Slider(start = 0, end = 30, 
                     step = 0.1, value = 10,
                     title = 'Radius scaler',
                       callback=CustomJS.from_py_func(radius_callback))

def range_callback(source=source, s2=s2, window=None):
    columns = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
               'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
               'Total Score', 'Latitude', 'Longitude', 'Critical', 'Radius']
    data = source.data
    data2 = s2.data        
    range_start = int(cb_obj.value[0])
    range_end = int(cb_obj.value[1])
    assert range_end > range_start
    for name in columns:
        data2[name] = []
    for name in columns:
        for i in range(range_start, range_end):
            data2[name].append(data[name][i])
    s2.change.emit()

selection = RangeSlider(start=1, end=2523, value=(1,2523), step=1, title="Structures",
                       callback=CustomJS.from_py_func(range_callback))



str0 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:River Bridge'])
str1 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Culvert'])
str2 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Subway'])
str3 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Footbridge'])
str4 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Retaining Wall'])
str5 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Pipe (Small Span Structure)'])
str6 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Sign/Gantry'])
str7 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Road Bridge'])
str8 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Viaduct'])
str9 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Underpass'])
str10 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Other'])
str11 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Embankment'])
str12 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Tunnel'])
str13 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Rail Bridge'])


def struc_callback(source=source, s2=s2, str0=str0, str1=str1, str3=str3, str4=str4,
                   str5=str5, str6=str6, str7=str7, str8=str8, str9=str9, str10=str10,
                   str11=str11, str12=str12, str13=str13, window=None):
    data = source.data
    data2 = s2.data
    length = len(data2['Structure Type'])
    value = cb_obj.value
    columns = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
               'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
               'Total Score', 'Latitude', 'Longitude', 'Critical', 'Radius']
    for name in columns:
        data2[name] = []
    for name in columns:
        for i in range(length):
            if value == 'S:River Bridge':
                data2[name] = str0.data[name]
            if value == 'S:Culvert':
                data2[name] = str1.data[name]
            if value == 'S:Subway':
                data2[name] = str2.data[name]
            if value == 'S:Footbridge':
                data2[name] = str3.data[name]
            if value == 'S:Retaining Wall':
                data2[name] = str4.data[name]
            if value == 'S:Pipe (Small Span Structure)':
                data2[name] = str5.data[name]
            if value == 'S:Sign/Gantry':
                data2[name] = str6.data[name]
            if value == 'S:Road Bridge':
                data2[name] = str7.data[name]
            if value == 'S:Viaduct':
                data2[name] = str8.data[name]
            if value == 'S:Underpass':
                data2[name] = str9.data[name]
            if value == 'S:Other':
                data2[name] = str10.data[name]
            if value == 'S:Embankment':
                data2[name] = str11.data[name]
            if value == 'S:Tunnel':
                data2[name] = str12.data[name]
            if value == 'S:Rail Bridge':
                data2[name] = str13.data[name]
            if value == 'All':
                data2[name] = data[name]
    s2.change.emit()

menu = [(struc, struc) for struc in DF_Sorted['Structure Type'].unique()]
menu.append(('All', 'All'))

struc_labels =[struc for struc in DF_Sorted['Structure Type'].unique()]

dropdown = Dropdown(label='Structure Type', menu=menu, button_type="success", callback=CustomJS.from_py_func(struc_callback))      


wanted_columns = ['feature_id', 'Name', 'Structure Type', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance',
               'Total Score']
columns = [TableColumn(field=str(value), title=value) for value in wanted_columns]
data_table = DataTable(source=source, columns=columns, width=1200, height=1000)


# Put controls in a single element
controls = WidgetBox(radius_select, selection, dropdown)

# Create a row layout

layout = row(controls, p, p2)

tab1 = Panel(child=layout, title="Plots")

tab2 = Panel(child=data_table, title="Data")

tabs = Tabs(tabs=[ tab1, tab2 ])

output_file("HCC Bridges Plot CARTODB.html", title='HCC Structures')

# show the results
# show(gridplot([[p, p_filtered]]))
show(tabs)

## Plot with Mercator projection and map background - CARTO

In [72]:
# prepare some data

x = DF_Sorted['Longitude'].values
y = DF_Sorted['Latitude'].values
axis_range = x.max()-x.min()
half_range = axis_range/2
y_mid = y.max() - (y.max()-y.min())/2
radii = Importance**2
color_list = [i for i in range(1, 101)]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(color_list))
]
map = {i:clr for i, clr in enumerate(colors)}


TOOLS = "crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,hover"

source = ColumnDataSource(DF_Sorted)
# source2 = ColumnDataSource(Merged[Merged['Importance'] >= 20])
s2 = ColumnDataSource(DF_Sorted)

s3 = ColumnDataSource({'x': [], 'y': [], 'width': [], 'height': []})

jscode="""
    var data = source.data;
    var start = cb_obj.start;
    var end = cb_obj.end;
    data['%s'] = [start + (end - start) / 2];
    data['%s'] = [end - start];
    source.change.emit();
"""

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below',
          x_axis_type="mercator", y_axis_type="mercator")

p.add_tile(CARTODBPOSITRON)

mapper = LinearColorMapper(palette=colors, low=1, high=100)

# add a circle renderer with vectorized colors and sizes
p.circle('Longitude', 'Latitude', source=s2, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.5, hover_alpha=0.8, line_color=None)


p.title.text = "HCC bridges"
p.title.align = "center"
p.title.text_color = "black"
p.title.text_font_size = "25px"

p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "0pt"
p.axis.major_label_standoff = 0

p.add_layout(Title(text="Colour Bar = Priority Score", align="center"), "right")

p.x_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('x', 'width'))
p.y_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('y', 'height'))

# create a new plot with the tools above, and explicit ranges
p2 = figure(tools='', x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below',
           x_axis_type="mercator", y_axis_type="mercator")

p2.add_tile(CARTODBPOSITRON)

# add a circle renderer with vectorized colors and sizes
p2.circle('Longitude', 'Latitude', source=source, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.5, hover_alpha=0.8, line_color=None)

# p_filtered = figure(tools=TOOLS, x_range=p.x_range, y_range=p.y_range, toolbar_location='below')
# p_filtered.circle('Easting', 'Northing', source=source2, radius='Radius', hover_color='red',
#          fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

p2.title.text = "See Zoom Window Here"
p2.title.align = "center"
p2.title.text_color = "black"
p2.title.text_font_size = "25px"

p2.axis.major_tick_line_color = None
p2.axis.major_label_text_font_size = "0pt"
p2.axis.major_label_standoff = 0

rect = Rect(x='x', y='y', width='width', height='height', fill_alpha=0.1,
            line_color='black', fill_color='black')

p2.add_glyph(s3, rect)

TOOLS="crosshair,pan,wheel_zoom,box_zoom,reset,hover"

hover =p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Importance", "@Importance"),
    ("BCI", "@Severity")])


color_bar = ColorBar(color_mapper=mapper, major_label_text_font_size="5pt",
                     ticker=BasicTicker(desired_num_ticks=int(len(colors)/5)),
                     label_standoff=6, border_line_color=None, location=(0, 0))



p.add_layout(color_bar, 'right')
# p_filtered.add_layout(color_bar2, 'right')

def radius_callback(source=s2, window=None):
    f=cb_obj.value
    data = source.data
    Imp = data['Importance']
    rad = data['Radius']
    for i in range(len(rad)):
        rad[i] = f*Imp[i]**1.5+100
    source.change.emit()

# Slider to select the radius scaler, value is selected number
radius_select = Slider(start = 0, end = 30, 
                     step = 0.1, value = 10,
                     title = 'Radius scaler',
                       callback=CustomJS.from_py_func(radius_callback))

def range_callback(source=source, s2=s2, window=None):
    columns = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
               'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
               'Total Score', 'Latitude', 'Longitude', 'Critical', 'Radius']
    data = source.data
    data2 = s2.data        
    range_start = int(cb_obj.value[0])
    range_end = int(cb_obj.value[1])
    assert range_end > range_start
    for name in columns:
        data2[name] = []
    for name in columns:
        for i in range(range_start, range_end):
            data2[name].append(data[name][i])
    s2.change.emit()

selection = RangeSlider(start=1, end=2523, value=(1,2523), step=1, title="Structures",
                       callback=CustomJS.from_py_func(range_callback))



str0 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:River Bridge'])
str1 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Culvert'])
str2 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Subway'])
str3 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Footbridge'])
str4 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Retaining Wall'])
str5 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Pipe (Small Span Structure)'])
str6 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Sign/Gantry'])
str7 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Road Bridge'])
str8 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Viaduct'])
str9 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Underpass'])
str10 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Other'])
str11 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Embankment'])
str12 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Tunnel'])
str13 = ColumnDataSource(DF_Sorted[DF_Sorted['Structure Type'] == 'S:Rail Bridge'])


def struc_callback(source=source, s2=s2, str0=str0, str1=str1, str3=str3, str4=str4,
                   str5=str5, str6=str6, str7=str7, str8=str8, str9=str9, str10=str10,
                   str11=str11, str12=str12, str13=str13, window=None):
    data = source.data
    data2 = s2.data
    length = len(data2['Structure Type'])
    value = cb_obj.value
    columns = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
               'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
               'Total Score', 'Latitude', 'Longitude', 'Critical', 'Radius']
    for name in columns:
        data2[name] = []
    for name in columns:
        for i in range(length):
            if value == 'S:River Bridge':
                data2[name] = str0.data[name]
            if value == 'S:Culvert':
                data2[name] = str1.data[name]
            if value == 'S:Subway':
                data2[name] = str2.data[name]
            if value == 'S:Footbridge':
                data2[name] = str3.data[name]
            if value == 'S:Retaining Wall':
                data2[name] = str4.data[name]
            if value == 'S:Pipe (Small Span Structure)':
                data2[name] = str5.data[name]
            if value == 'S:Sign/Gantry':
                data2[name] = str6.data[name]
            if value == 'S:Road Bridge':
                data2[name] = str7.data[name]
            if value == 'S:Viaduct':
                data2[name] = str8.data[name]
            if value == 'S:Underpass':
                data2[name] = str9.data[name]
            if value == 'S:Other':
                data2[name] = str10.data[name]
            if value == 'S:Embankment':
                data2[name] = str11.data[name]
            if value == 'S:Tunnel':
                data2[name] = str12.data[name]
            if value == 'S:Rail Bridge':
                data2[name] = str13.data[name]
            if value == 'All':
                data2[name] = data[name]
    s2.change.emit()

menu = [(struc, struc) for struc in DF_Sorted['Structure Type'].unique()]
menu.append(('All', 'All'))

struc_labels =[struc for struc in DF_Sorted['Structure Type'].unique()]

dropdown = Dropdown(label='Structure Type', menu=menu, button_type="success", callback=CustomJS.from_py_func(struc_callback))      


wanted_columns = ['feature_id', 'Name', 'Structure Type', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance',
               'Total Score']
columns = [TableColumn(field=str(value), title=value) for value in wanted_columns]
data_table = DataTable(source=source, columns=columns, width=1200, height=1000)


# Put controls in a single element
controls = WidgetBox(radius_select, selection, dropdown)

# Create a row layout

layout = row(controls, p, p2)

tab1 = Panel(child=layout, title="Plots")

tab2 = Panel(child=data_table, title="Data")

tabs = Tabs(tabs=[ tab1, tab2 ])

output_file("HCC Bridges Plot - Carto.html")

# show the results
# show(gridplot([[p, p_filtered]]))
show(tabs)

ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name: Latitude, Longitude, Radius [renderer: GlyphRenderer(id='24ee5601-7042-4b07-a1e9-9c29a02dd6ff', ...)]
ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name: Latitude, Longitude, Radius [renderer: GlyphRenderer(id='2aa940d6-43b4-40cc-9199-3d97cb13d3ec', ...)]
ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name: Latitude, Longitude, Radius [renderer: GlyphRenderer(id='30b14edf-aff7-4b34-96bf-591677baba46', ...)]
ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name: Latitude, Longitude, Radius [renderer: GlyphRenderer(id='3a26c074-f4b0-4cab-b1ef-93b795cc6ad7', ...)]
ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name: Latitude, Longitude, Radius [renderer: GlyphRenderer(id='4347e0ff-4a1a-4c9e-85f2-6b1732

## Bridge Atlas

In [43]:
DF_Sorted['Radius'] = 100
DF_Sorted['Structure Type'].unique()

array(['S:River Bridge', 'S:Culvert', 'S:Subway', 'S:Footbridge',
       'S:Retaining Wall', 'S:Pipe (Small Span Structure)',
       'S:Sign/Gantry', 'S:Road Bridge', 'S:Viaduct', 'S:Underpass',
       'S:Other', 'S:Embankment', 'S:Tunnel', 'S:Rail Bridge'],
      dtype=object)

In [44]:
struc_frames = []
source_frames = []
sources = []

In [45]:
for i, struc in enumerate(DF_Sorted['Structure Type'].unique()):
    struc_frames.append(DF_Sorted[DF_Sorted['Structure Type'] == struc])

In [46]:
for i, src in enumerate(struc_frames):
    sources.append(ColumnDataSource(src))

In [47]:
# prepare some data

x = DF_Sorted['Longitude'].values
y = DF_Sorted['Latitude'].values
# radii = Importance**2
# color_list = [i for i in range(1, 101)]
colors = Category20[14]
# map = {i:clr for i, clr in enumerate(colors)}

circles = []

TOOLS = "crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,hover"

# source = ColumnDataSource(DF_Sorted)
# source2 = ColumnDataSource(Merged[Merged['Importance'] >= 20])
s2 = ColumnDataSource(DF_Sorted)

s3 = ColumnDataSource({'x': [], 'y': [], 'width': [], 'height': []})

jscode="""
    var data = source.data;
    var start = cb_obj.start;
    var end = cb_obj.end;
    data['%s'] = [start + (end - start) / 2];
    data['%s'] = [end - start];
    source.change.emit();
"""

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below',
          x_axis_type="mercator", y_axis_type="mercator")

p.add_tile(STAMEN_TERRAIN)

mapper = CategoricalColorMapper(palette=colors, factors=Struc_uniq)

for data, name, color in zip(sources, Struc_uniq, colors):
    circles.append(p.circle('Longitude', 'Latitude', radius='Radius', source=data, color=color, alpha=0.8, legend=name))

# # add a circle renderer with vectorized colors and sizes
# p.circle('Longitude', 'Latitude', source=s2, radius='Radius', hover_color='red',
#          fill_color={'field': 'Structure Type', 'transform': mapper}, fill_alpha=0.5, hover_alpha=0.8, line_color=None)


p.title.text = "HCC Bridge Atlas"
p.title.align = "center"
p.title.text_color = "black"
p.title.text_font_size = "25px"



p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "0pt"
p.axis.major_label_standoff = 0

p.x_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('x', 'width'))
p.y_range.callback = CustomJS(
        args=dict(source=s3), code=jscode % ('y', 'height'))

# create a new plot with the tools above, and explicit ranges
# p2 = figure(tools='', x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below',
#            x_axis_type="mercator", y_axis_type="mercator")

# p2.add_tile(STAMEN_TERRAIN)

# p2.title.text = "See Zoom Window Here"
# p2.title.align = "center"
# p2.title.text_color = "black"
# p2.title.text_font_size = "25px"

# p2.axis.major_tick_line_color = None
# p2.axis.major_label_text_font_size = "0pt"
# p2.axis.major_label_standoff = 0

# rect = Rect(x='x', y='y', width='width', height='height', fill_alpha=0.1,
#             line_color='black', fill_color='black')

# p2.add_glyph(s3, rect)

TOOLS="crosshair,pan,wheel_zoom,box_zoom,reset,hover"

hover =p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Northing", "@Northing"),
    ("Easting", "@Easting")])


legend = Legend(items=[
    (Struc_uniq[0]   , [circles[0]]),
    (Struc_uniq[1]   , [circles[1]]),
    (Struc_uniq[2]   , [circles[2]]),
    (Struc_uniq[3]   , [circles[3]]),
    (Struc_uniq[4]   , [circles[4]]),
    (Struc_uniq[5]   , [circles[5]]),
    (Struc_uniq[6]   , [circles[6]]),
    (Struc_uniq[7]   , [circles[7]]),
    (Struc_uniq[8]   , [circles[8]]),
    (Struc_uniq[9]   , [circles[9]]),
    (Struc_uniq[10]   , [circles[10]]),
    (Struc_uniq[11]   , [circles[11]]),
    (Struc_uniq[12]   , [circles[12]]),
    (Struc_uniq[13]   , [circles[13]])
], location=(0, 0))

p.legend.visible = not legend.visible

def struc_callback(source=source, s2=s2, str0=str0, str1=str1, str3=str3, str4=str4,
                   str5=str5, str6=str6, str7=str7, str8=str8, str9=str9, str10=str10,
                   str11=str11, str12=str12, str13=str13, window=None):
    data = source.data
    data2 = s2.data
    length = len(data2['Structure Type'])
    value = cb_obj.value
    columns = ['feature_id', 'Name', 'Structure Type', 'Status', 'Easting', 'Northing',
               'Maintaining Agent', 'Construction Year', 'Hertitage', 'critical_bci',
               'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
               'Carries Score', 'Route Score', 'BCI Score', 'Importance', 'Severity',
               'Total Score', 'Latitude', 'Longitude', 'Critical', 'Radius']
    for name in columns:
        data2[name] = []
    for name in columns:
        for i in range(length):
            if value == 'S:River Bridge':
                data2[name] = str0.data[name]
            if value == 'S:Culvert':
                data2[name] = str1.data[name]
            if value == 'S:Subway':
                data2[name] = str2.data[name]
            if value == 'S:Footbridge':
                data2[name] = str3.data[name]
            if value == 'S:Retaining Wall':
                data2[name] = str4.data[name]
            if value == 'S:Pipe (Small Span Structure)':
                data2[name] = str5.data[name]
            if value == 'S:Sign/Gantry':
                data2[name] = str6.data[name]
            if value == 'S:Road Bridge':
                data2[name] = str7.data[name]
            if value == 'S:Viaduct':
                data2[name] = str8.data[name]
            if value == 'S:Underpass':
                data2[name] = str9.data[name]
            if value == 'S:Other':
                data2[name] = str10.data[name]
            if value == 'S:Embankment':
                data2[name] = str11.data[name]
            if value == 'S:Tunnel':
                data2[name] = str12.data[name]
            if value == 'S:Rail Bridge':
                data2[name] = str13.data[name]
            if value == 'All':
                data2[name] = data[name]
    s2.change.emit()

menu = [(struc, struc) for struc in DF_Sorted['Structure Type'].unique()]
menu.append(('All', 'All'))

struc_labels =[struc for struc in DF_Sorted['Structure Type'].unique()]

dropdown = Dropdown(label='Structure Type', menu=menu, button_type="success", callback=CustomJS.from_py_func(struc_callback))      

struc_selection = CheckboxGroup(labels=list(Merged['Structure Type'].unique()),
                                active=[i for i in range(len(Struc_uniq))], callback=CustomJS.from_py_func(struc_callback))



# p.legend.location = "top_left"
# p.legend.click_policy="hide"
# p.legend.orientation = "horizontal"
   


# wanted_columns = ['feature_id', 'Name', 'Structure Type', 'critical_bci',
#                'length', 'Carries', 'Crosses', 'Length Score', 'Crosses Score',
#                'Carries Score', 'Route Score', 'BCI Score', 'Importance',
#                'Total Score']
# columns = [TableColumn(field=str(value), title=value) for value in wanted_columns]
# data_table = DataTable(source=source, columns=columns, width=1200, height=1000)


# # Put controls in a single element
# controls = WidgetBox(radius_select)

# # Create a row layout
# p2.add_layout(legend, 'right')

# p.legend.__setattr__('label_text_font_size', "5pt")
# p.legend.__setattr__('glyph_height', 10)
# p.legend.__setattr__('glyph_width', 10)
# p.legend.__setattr__('label_height', 10)
# p.legend.__setattr__('label_width', 20)

controls = WidgetBox(radius_select)

layout = row(p, p2)

# tab1 = Panel(child=layout, title="Plots")

# tab2 = Panel(child=data_table, title="Data")

# tabs = Tabs(tabs=[ tab1, tab2 ])

output_file("HCC Bridge Atlas.html")

# show the results
# show(gridplot([[p, p_filtered]]))

show(layout)

IndexError: list index out of range

In [38]:
DF_Sorted['Structure Type'].unique()

array(['S:River Bridge', 'S:Culvert', 'S:Subway', 'S:Footbridge',
       'S:Retaining Wall', 'S:Pipe (Small Span Structure)',
       'S:Sign/Gantry', 'S:Road Bridge', 'S:Viaduct', 'S:Underpass',
       'S:Other', 'S:Embankment', 'S:Tunnel', 'S:Rail Bridge'],
      dtype=object)

In [46]:
# prepare some data

x = Merged['Easting'].values
y = Merged['Northing'].values
axis_range = x.max()-x.min()
half_range = axis_range/2
y_mid = y.max() - (y.max()-y.min())/2
radii = Importance**2
color_list = [i for i in range(1, 101)]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(color_list))
]
map = {i:clr for i, clr in enumerate(colors)}


TOOLS = "crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,hover"

source = ColumnDataSource(Merged[Merged['Importance'] >= 20])
# source2 = ColumnDataSource(Merged[Merged['Importance'] >= 20])
# s2 = ColumnDataSource(data={key: [] for key in Merged.keys()})

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below')

# p.add_tile(STAMEN_TERRAIN)

mapper = LinearColorMapper(palette=colors, low=1, high=100)

# add a circle renderer with vectorized colors and sizes
p.circle('Easting', 'Northing', source=source, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

# p_filtered = figure(tools=TOOLS, x_range=p.x_range, y_range=p.y_range, toolbar_location='below')
# p_filtered.circle('Easting', 'Northing', source=source2, radius='Radius', hover_color='red',
#          fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

p.title.text = "Non-critical bridges"
p.title.align = "center"
p.title.text_color = "black"
p.title.text_font_size = "25px"



p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "0pt"
p.axis.major_label_standoff = 0

# p_filtered.title.text = "Critical Bridges"
# p_filtered.title.align = "center"
# p_filtered.title.text_color = "black"
# p_filtered.title.text_font_size = "25px"

# p_filtered.axis.major_tick_line_color = None
# p_filtered.axis.major_label_text_font_size = "0pt"
# p_filtered.axis.major_label_standoff = 0



TOOLS="crosshair,pan,wheel_zoom,box_zoom,reset,hover"

hover =p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Importance", "@Importance"),
    ("BCI", "@Severity")])


color_bar = ColorBar(color_mapper=mapper, major_label_text_font_size="5pt",
                     ticker=BasicTicker(desired_num_ticks=int(len(colors)/5)),
                     label_standoff=6, border_line_color=None, location=(0, 0))



p.add_layout(color_bar, 'right')
# p_filtered.add_layout(color_bar2, 'right')

def radius_callback(source=source, window=None):
    f=cb_obj.value
    data = source.data
    Imp = data['Importance']
    rad = data['Radius']
    for i in range(len(rad)):
        rad[i] = f*Imp[i]**1.5+50
    source.change.emit()

# Slider to select the radius scaler, value is selected number
radius_select = Slider(start = 0, end = 10, 
                     step = 0.1, value = 1,
                     title = 'Radius scaler',
                       callback=CustomJS.from_py_func(radius_callback))


# Update the plot when the value is changed
# radius_select.on_change('value', update)

# def callback(source=source):
#     data = source.data
#     f = cb_obj.active
#     struc = data['Structure Type']
#     imp = data['Importance']
#     for i in range(len(imp)):
#         if struc[i] in f:
#             data['Importance'] = 0
#             data['Radius'] = 0
#     source.change.emit()

# struc_selection = CheckboxGroup(labels=list(Merged['Structure Type'].unique()),
#                                 active=[i for i in range(len(Merged['Structure Type'].unique()))], callback=CustomJS.from_py_func(struc_callback))


# struc_selection.on_change('active', struc_callback)

# def struc_callback(source=source, window=None):
#     act = [cb_obj.labels[i] for i in cb_obj.active]
#     data = source.data
#     Imp = data['Importance']
#     rad = data['Radius']
#     for i in range(len(rad)):
#         rad[i] = f*Imp[i]**2+100
#     source.change.emit()

# crit_select = Button(
#         label="Critical", button_type="success", callback=CustomJS.from_py_func(crit_callback))

# crit_select.js_on_click(crit_callback)

# crit_callback = CustomJS(args=dict(s2=s2), code="""
#         var inds = cb_obj.selected.indices;
#         var d1 = cb_obj.data;
#         var d2 = s2.data;
#         d2['x'] = []
#         d2['y'] = []
#         for (var i = 0; i < inds.length; i++) {
#             d2['x'].push(d1['x'][inds[i]])
#             d2['y'].push(d1['y'][inds[i]])
#         }
#         s2.change.emit();
#     """)

# crit_select.on_change('active', update)

# Put controls in a single element
controls = WidgetBox(radius_select)

# Create a row layout

layout = row(controls, p)

# tab1 = Panel(child=layout1, title="Non-Critical")

# tab2 = Panel(child=layout2, title="Critical")

# tabs = Tabs(tabs=[ tab1, tab2 ])

output_file("HCC Bridges Critical.html")

# show the results
# show(gridplot([[p, p_filtered]]))
show(layout)

In [37]:
# prepare some data

x = Merged['Easting'].values
y = Merged['Northing'].values
radii = Importance**2+50
color_list = [i for i in range(1, 101)]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(color_list))
]
map = {i:clr for i, clr in enumerate(colors)}
# filter_color = []
# for i, bl in enumerate(Merged['Critical'].values):
#     if bl == True:
#         filter_color.append(colors[i])

# output to static HTML file (with CDN resources)
# output_file("color_scatter.html", title="color_scatter.py example", mode="cdn")

# hover = HoverTool(tooltips=[("Easting", "@x"), ("y", "@y")])

TOOLS = "crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,hover"

source = ColumnDataSource(Merged[Merged['Importance'] < 20])
source2 = ColumnDataSource(Merged[Merged['Importance'] >= 20])
s2 = ColumnDataSource(data={key: [] for key in Merged.keys()})

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(x.min()-100, x.max()+100), y_range=(y.min()-100, y.max()+100), toolbar_location='below')

mapper = LinearColorMapper(palette=colors, low=1, high=100)

# add a circle renderer with vectorized colors and sizes
p.circle('Easting', 'Northing', source=source, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

p_filtered = figure(tools=TOOLS, x_range=p.x_range, y_range=p.y_range)
p_filtered.circle('Easting', 'Northing', source=source2, radius='Radius', hover_color='red',
         fill_color={'field': 'Total Score', 'transform': mapper}, fill_alpha=0.3, hover_alpha=0.8, line_color=None)

p.title.text = "Non-critical bridges"
p.title.align = "center"
p.title.text_color = "black"
p.title.text_font_size = "25px"

tab1 = Panel(child=p, title="circle")

p.axis.major_tick_line_color = None
p.axis.major_label_text_font_size = "0pt"
p.axis.major_label_standoff = 0

p_filtered.title.text = "Critical Bridges"
p_filtered.title.align = "center"
p_filtered.title.text_color = "black"
p_filtered.title.text_font_size = "25px"

p_filtered.axis.major_tick_line_color = None
p_filtered.axis.major_label_text_font_size = "0pt"
p_filtered.axis.major_label_standoff = 0

tab2 = Panel(child=p_filtered, title="line")

TOOLS="crosshair,pan,wheel_zoom,box_zoom,reset,hover"

hover =p.select(dict(type=HoverTool))
hover.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Importance", "@Importance"),
    ("BCI", "@Severity")])

hover2 =p_filtered.select(dict(type=HoverTool))
hover2.tooltips = OrderedDict([
    ("Struct ID", "@feature_id"),
    ("Name", "@Name"),
    ("Importance", "@Importance"),
    ("BCI", "@Severity")])

color_bar = ColorBar(color_mapper=mapper, major_label_text_font_size="5pt",
                     ticker=BasicTicker(desired_num_ticks=int(len(colors)/5)),
                     label_standoff=6, border_line_color=None, location=(0, 0))


p.add_layout(color_bar, 'right')

def radius_callback(source=source, window=None):
    f=cb_obj.value
    data = source.data
    Imp = data['Importance']
    rad = data['Radius']
    for i in range(len(rad)):
        rad[i] = f*Imp[i]**2+100
    source.change.emit()

# Slider to select the radius scaler, value is selected number
radius_select = Slider(start = 0, end = 10, 
                     step = 0.1, value = 1,
                     title = 'Radius scaler',
                       callback=CustomJS.from_py_func(radius_callback))


# Update the plot when the value is changed
# radius_select.on_change('value', update)

# def callback(source=source):
#     data = source.data
#     f = cb_obj.active
#     struc = data['Structure Type']
#     imp = data['Importance']
#     for i in range(len(imp)):
#         if struc[i] in f:
#             data['Importance'] = 0
#             data['Radius'] = 0
#     source.change.emit()

# struc_selection = CheckboxGroup(labels=list(Merged['Structure Type'].unique()),
#                                 active=[i for i in range(len(Merged['Structure Type'].unique()))], callback=CustomJS.from_py_func(struc_callback))


# struc_selection.on_change('active', struc_callback)

# def struc_callback(source=source, window=None):
#     act = [cb_obj.labels[i] for i in cb_obj.active]
#     data = source.data
#     Imp = data['Importance']
#     rad = data['Radius']
#     for i in range(len(rad)):
#         rad[i] = f*Imp[i]**2+100
#     source.change.emit()

# crit_select = Button(
#         label="Critical", button_type="success", callback=CustomJS.from_py_func(crit_callback))

# crit_select.js_on_click(crit_callback)

# crit_callback = CustomJS(args=dict(s2=s2), code="""
#         var inds = cb_obj.selected.indices;
#         var d1 = cb_obj.data;
#         var d2 = s2.data;
#         d2['x'] = []
#         d2['y'] = []
#         for (var i = 0; i < inds.length; i++) {
#             d2['x'].push(d1['x'][inds[i]])
#             d2['y'].push(d1['y'][inds[i]])
#         }
#         s2.change.emit();
#     """)

# crit_select.on_change('active', update)

# Put controls in a single element
controls = WidgetBox(radius_select)

# Create a row layout
layout = row(controls, p, p_filtered)

# tabs = Tabs(tabs=[ tab1, tab2 ])

output_file("HCC Bridges.html")

# show the results
# show(gridplot([[p, p_filtered]]))
show(tabs)